## Problem Statement

We have been given a ODE: 

$$
\frac{d^2x(t)}{dt^2} = - k x(t)
$$

The ODE can be writen, like:

$$
\frac{d^2x(t)}{dt^2} + k x(t) = 0
$$
<!---
(du/dx=2du/dt+u)
-->

and boundary condition: 

$$
x(0) = 0
$$
<!---
u(x,0)=6e^(-3x)
-->


- Independent variables: t (input)
- Dependent variables: x,y (outputs)


We have to find out u(x,t) for all t in range [0,20]

In [1]:
import numpy as np
import plotly.graph_objects as go

import torch
import torch.nn as nn
from torch.autograd import Variable
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [2]:
def build_model(input_dimension, hidden_dimension, output_dimension):

    modules=[]
    modules.append(torch.nn.Linear(input_dimension, hidden_dimension[0]))
    modules.append(torch.nn.Tanh())
    for i in range(len(hidden_dimension)-1):
        modules.append(torch.nn.Linear(hidden_dimension[i], hidden_dimension[i+1]))
        modules.append(torch.nn.Tanh())
    
    modules.append(torch.nn.Linear(hidden_dimension[-1], output_dimension))
    
    model = torch.nn.Sequential(*modules)

    return model

net = build_model(1,[50, 50, 20, 20],1)
net = net.to(device)
mse_cost_function = torch.nn.MSELoss()
optimizer = torch.optim.Adam(net.parameters())

def get_derivative(x, t, n=1):
    
    if n == 0:
        return x
    else:
        
        dxdt = torch.autograd.grad(x, t, torch.ones(t.size()[0], 1, device=device),
        create_graph=True,
        retain_graph=True, 
        )[0]
    return get_derivative(dxdt, t, n - 1)


def f(t, net, k):
    u = net(t)
    dudtdt = get_derivative(u, t, 2)
    ode = dudtdt + k*u
    return ode

k = torch.tensor([[3]], dtype=torch.float32, device=device)
init_t = torch.tensor([[0]], dtype=torch.float32, device=device)
init_x = torch.tensor([[5]], dtype=torch.float32, device=device)

n_points = 5000
t_collocation = np.linspace(0, 20, n_points).reshape(-1,1)
all_zeros = np.zeros((n_points,1))

pt_t_collocation = Variable(torch.from_numpy(t_collocation).float(), requires_grad=True).to(device)
pt_all_zeros = Variable(torch.from_numpy(all_zeros).float(), requires_grad=True).to(device)

iterations = 100000
loss_count = []
loss_boundary = []
loss_func = []

for epoch in range(iterations):
    optimizer.zero_grad()

    init_pred = net(init_t)
    mse_b = mse_cost_function(init_pred, init_x)
    
    f_out = f(pt_t_collocation, net,k) 
    mse_f = mse_cost_function(f_out, pt_all_zeros)
    
    loss = mse_b + mse_f
    
    loss_boundary.append(mse_b.item())
    loss_func.append(mse_f.item())
    loss_count.append(loss.item())

    loss.backward(retain_graph=True) 
    optimizer.step() 

    with torch.autograd.no_grad():
        if epoch % 100 ==0:
    	    print(epoch,"Traning Loss:",loss.data)

f_out = net(pt_t_collocation)

xx = f_out[:, 0].data.cpu().numpy()

0 Traning Loss: tensor(24.8679, device='cuda:0')
100 Traning Loss: tensor(3.9329, device='cuda:0')
200 Traning Loss: tensor(2.2698, device='cuda:0')
300 Traning Loss: tensor(1.8415, device='cuda:0')
400 Traning Loss: tensor(1.6934, device='cuda:0')
500 Traning Loss: tensor(1.5902, device='cuda:0')
600 Traning Loss: tensor(1.5461, device='cuda:0')
700 Traning Loss: tensor(1.5278, device='cuda:0')
800 Traning Loss: tensor(1.5000, device='cuda:0')
900 Traning Loss: tensor(1.5203, device='cuda:0')
1000 Traning Loss: tensor(1.4622, device='cuda:0')
1100 Traning Loss: tensor(1.4449, device='cuda:0')
1200 Traning Loss: tensor(1.4229, device='cuda:0')
1300 Traning Loss: tensor(1.4049, device='cuda:0')
1400 Traning Loss: tensor(1.3866, device='cuda:0')
1500 Traning Loss: tensor(1.3762, device='cuda:0')
1600 Traning Loss: tensor(1.3632, device='cuda:0')
1700 Traning Loss: tensor(1.3814, device='cuda:0')
1800 Traning Loss: tensor(1.3439, device='cuda:0')
1900 Traning Loss: tensor(1.3349, device='

In [3]:
net

Sequential(
  (0): Linear(in_features=1, out_features=50, bias=True)
  (1): Tanh()
  (2): Linear(in_features=50, out_features=50, bias=True)
  (3): Tanh()
  (4): Linear(in_features=50, out_features=20, bias=True)
  (5): Tanh()
  (6): Linear(in_features=20, out_features=20, bias=True)
  (7): Tanh()
  (8): Linear(in_features=20, out_features=1, bias=True)
)

In [4]:
loss

tensor(0.0012, device='cuda:0', grad_fn=<AddBackward0>)

In [5]:
fig = go.Figure()
fig.add_scatter(x = t_collocation.flatten(), y=xx)

In [6]:
fig = go.Figure()
fig.add_scatter(y = loss_count)

In [7]:
fig = go.Figure()
fig.add_scatter(y = loss_boundary)

In [8]:
fig = go.Figure()
fig.add_scatter(y = loss_func)

In [9]:
t_collocation = np.linspace(0, 100, n_points).reshape(-1,1)
pt_t_collocation = Variable(torch.from_numpy(t_collocation).float(), requires_grad=True).to(device)
f_out = net(pt_t_collocation)
xx = f_out[:, 0].data.cpu().numpy()

fig = go.Figure()
fig.add_scatter(x = t_collocation.flatten(), y=xx)